In [8]:
import json
import pandas as pd
import numpy as np 
import xml.etree.ElementTree as ET
from bs4 import BeautifulSoup
import random
from random import choices
from lxml import etree
from xml.dom import minidom

from os import listdir
from os.path import isfile, join

import multiprocessing

In [94]:
df_HH = pd.read_csv('Synthetic Population/HH_data_1mil.csv')
df_P = pd.read_csv('Synthetic Population/Person_data_1mil.csv')
# df_flight = pd.read_csv('buildXML/flights.csv')
df_book = pd.read_csv('buildXML/bookings.csv')
crosswalk = pd.read_csv('GeoCrosswalk.csv')
df_HH_POI = pd.read_csv('buildXML/HH_POI.csv')
df_P_POI = pd.read_csv('buildXML/P_POI.csv')
df_flight = pd.read_csv('buildXML/flights_POI.csv')
df_book_POI = pd.read_csv('buildXML/bookings_POI.csv')

/Users/muhammadfathifadlian/opt/anaconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3185: DtypeWarning: Columns (11) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/Users/muhammadfathifadlian/opt/anaconda3/lib/python3.9/site-packages/IPython/core/interactiveshell.py:3185: DtypeWarning: Columns (18) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [95]:
df_HH = df_HH.append(df_HH_POI, ignore_index=True)
df_P = df_P.append(df_P_POI, ignore_index=True)
# df_flight = df_flight.append(df_flight_POI, ignore_index=True)
df_book = df_book.append(df_book_POI, ignore_index=True)

In [83]:
mypath = 'XML_DATAV2'
onlyfiles = [f for f in listdir(mypath) if isfile(join(mypath, f))]

suffix_to_remove = '.xml'
 
# Suffix removal from String list
# using loop + remove() + endswith()
new_files = [s.replace(suffix_to_remove, "") for s in onlyfiles]
if '.DS_Store' in new_files:
    new_files.remove('.DS_Store')
    
int_list = [int(item) for item in new_files]

In [84]:
len(int_list)

14806

In [69]:
len(new_files)

5375

In [98]:
def df_flight_clean(df_flight):
    df_flight['bookings'] = df_flight['bookings'].str.replace("[", "")
    df_flight['bookings'] = df_flight['bookings'].str.replace("]", "")
    df_flight['bookings'] = df_flight['bookings'].str.replace("'", "")
    df_flight['bookings'] = df_flight['bookings'].str.replace(" ", "")
    

    return df_flight

df_flight = df_flight_clean(df_flight)

In [99]:
def df_book_clean(df_book, crosswalk):
    df_book['Airport_Itinerary_Out'] = df_book['Airport_Itinerary_Out'].str.replace("[", "")
    df_book['Airport_Itinerary_Out'] = df_book['Airport_Itinerary_Out'].str.replace("]", "")
    df_book['Airport_Itinerary_Out'] = df_book['Airport_Itinerary_Out'].str.replace("'", "")
    df_book['Airport_Itinerary_Out'] = df_book['Airport_Itinerary_Out'].str.replace(" ", "")
    df_book['Airport_Itinerary_Out'] = df_book['Airport_Itinerary_Out'].str.split(",")
    df_book['IATA'] = df_book['Airport_Itinerary_Out'].str.get(0)
    cw = crosswalk[['IATA', 'Currency', 'HH_ISO', 'City']].copy()
    df_book = df_book.merge(cw, on = 'IATA', how = 'left')
    
    df_book['list_of_passengers'] = df_book['list_of_passengers'].str.replace("[", "")
    df_book['list_of_passengers'] = df_book['list_of_passengers'].str.replace("]", "")
    df_book['list_of_passengers'] = df_book['list_of_passengers'].str.replace("'", "")
    df_book['list_of_passengers'] = df_book['list_of_passengers'].str.replace(" ", "")
    df_book['list_of_passengers'] = df_book['list_of_passengers'].str.split(",")
    df_book['primary_passengers'] = df_book['list_of_passengers'].str.get(0)
    
    df_book['outboundFlights'] = df_book['outboundFlights'].str.replace("[", "")
    df_book['outboundFlights'] = df_book['outboundFlights'].str.replace("]", "")
    df_book['outboundFlights'] = df_book['outboundFlights'].str.replace("'", "")
    df_book['outboundFlights'] = df_book['outboundFlights'].str.replace(" ", "")
    df_book['outboundFlights'] = df_book['outboundFlights'].str.split(",")
    
    df_book['returnFlights'] = df_book['returnFlights'].str.replace("[", "")
    df_book['returnFlights'] = df_book['returnFlights'].str.replace("]", "")
    df_book['returnFlights'] = df_book['returnFlights'].str.replace("'", "")
    df_book['returnFlights'] = df_book['returnFlights'].str.replace(" ", "")
    df_book['returnFlights'] = df_book['returnFlights'].str.split(",")
    
    df_book['allFlights'] = df_book['outboundFlights'] + df_book['returnFlights']
    string_to_remove = 'nan'
    df_book['allFlights'] = df_book['allFlights'].apply(lambda x: [item for item in x if item != string_to_remove])
    df_book['allFlights'] = df_book['allFlights'].apply(lambda x: [int(item) for item in x])
    df_book['allFlights'] = df_book['allFlights'].apply(lambda x: [item for item in x if not pd.isna(item)])
    return df_book
df_book = df_book_clean(df_book, crosswalk)

In [72]:
df_flight = df_flight[df_flight['retPNRs'] != 0]
df_flight.groupby('retPNRs')['callsign'].count().reset_index()

retPNRs  callsign
0         1     14739
1         2      9394
2         3      6487
3         4      4939
4         5      3997
..      ...       ...
84       93         1
85       97         1
86      107         1
87      111         1
88      113         1

[89 rows x 2 columns]

In [85]:
flight_ids = df_flight['flight_id'].tolist()
flight_ids = [x for x in flight_ids if x not in int_list]
len(flight_ids)

51180

In [49]:
flight_ids = [141248, 74802, 151717, 153090, 53398, 184710, 185978, 217108]

In [25]:
from joblib import Parallel, delayed
import time, math

In [86]:
Parallel(n_jobs=6)(delayed(PNRGeneration)(i) for i in flight_ids)

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


...

Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


KeyboardInterrupt: 

In [64]:
def PNRGeneration(i):
    
    root = ET.Element("IATA_PNRGOV_NotifRQ")      
    a1 = ET.Element("Originator")
    a1.set('AirlineCode', str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
    a1.set('SystemCode', 'SYSTEMCODE')
    a1.set('AirlineContactInfo', 'AIRLINE CONTACT INFO')
    root.append(a1)
    
    a2 = ET.Element('FlightLeg')
    a2.set('CarrierCode', str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
    a2.set('FlightNumber', str(df_flight.loc[df_flight['flight_id'] == i, 'flightNbr'].iloc[0]))
    a2.set('DepartureDateTime', str(df_flight.loc[df_flight['flight_id'] == i, 'firstseen'].iloc[0]))
    a2.set('ArrivalDateTime', str(df_flight.loc[df_flight['flight_id'] == i, 'lastseen'].iloc[0]))
    a2.set('DateChangeNbr', str(pd.Timedelta(pd.to_datetime(df_flight.loc[df_flight['flight_id'] == i, 'lastseen'].iloc[0]) - pd.to_datetime(df_flight.loc[df_flight['flight_id'] == i, 'firstseen'].iloc[0])).days))
    
    a2_1 = ET.SubElement(a2, 'DepartureAirport')
    a2_1.set('LocationCode', df_flight.loc[df_flight['flight_id'] == i, 'IATA_O'].iloc[0])
    a2_2 = ET.SubElement(a2, 'ArrivalAirport')
    a2_2.set('LocationCode', df_flight.loc[df_flight['flight_id'] == i, 'IATA_D'].iloc[0])
    root.append(a2)
    
    a3 = ET.Element('PNRs', NumberOfPnrs = str(df_flight.loc[df_flight['flight_id'] == i, 'retPNRs'].iloc[0]))
    root.append(a3)
    
#     print(i)
    for j in df_flight.loc[df_flight['flight_id'] == i, 'bookings'].iloc[0].split(","):
#         print(j)
        a3_1 = ET.SubElement(a3, 'PNR', NumberOfPassengers = str(df_book.loc[df_book['initID'] == j, 'num_in_party'].iloc[0]), 
                             PNR_TransDate = str(pd.to_datetime(df_book.loc[df_book['initID'] == j, 'outboundDate'].iloc[0]) - pd.Timedelta('10 days ')),
                             PNR_CreationDate = str(pd.to_datetime(df_book.loc[df_book['initID'] == j, 'outboundDate'].iloc[0]) - pd.Timedelta('10 days ')),
                             LastTktDate = str(pd.to_datetime(df_book.loc[df_book['initID'] == j, 'outboundDate'].iloc[0]) - pd.Timedelta('10 days ')))
        
        a3_1_1 = ET.SubElement(a3_1, 'BookingRefID', ID=str(j))
        a3_1_1_1 = ET.SubElement(a3_1_1, 'CompanyName', 
                                 TravelSector = 'TravelSectorCode', 
                                 Code = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
                
        a3_1_2 = ET.SubElement(a3_1, 'POS')
        a3_1_2_1 = ET.SubElement(a3_1_2, 'Source', AgentSine = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]),
                                PseudoCityCode = str(df_book.loc[df_book['initID'] == j, 'City'].iloc[0]),
                                ISOCOuntry = str(df_book.loc[df_book['initID'] == j, 'HH_ISO'].iloc[0]),
                                ISOCurrency = str(df_book.loc[df_book['initID'] == j, 'Currency'].iloc[0]),
                                AgentDutyCode = "-",
                                AirlineVendorID = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]),
                                AirportCode = str(df_book.loc[df_book['initID'] == j, 'IATA'].iloc[0]))
        a3_1_2_1_1 = ET.SubElement(a3_1_2_1, 'RequestorID', ID = "REQUESTOR ID")
        a3_1_2_1_1_1 = ET.SubElement(a3_1_2_1_1, 'CompanyName', Code = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
        
        for k in df_book.loc[df_book['initID'] == j, 'list_of_passengers'].iloc[0]:
#             print(k)
            a3_1_3 = ET.SubElement(a3_1, 'Passenger', RPH = k,
                                   SurnameRefNumber = str(df_P.loc[df_P['P_ID'] == k, 'HHID'].iloc[0]),
                                   BoardingStatus = "63")
            a3_1_3_1 = ET.SubElement(a3_1_3, 'GivenName')
            a3_1_3_1.text = str(df_P.loc[df_P['P_ID'] == k, 'FirstName'].iloc[0])
            a3_1_3_2 = ET.SubElement(a3_1_3, 'Surname')
            a3_1_3_2.text = str(df_P.loc[df_P['P_ID'] == k, 'Surname'].iloc[0])
            a3_1_3_3 = ET.SubElement(a3_1_3, 'CustLoyalty', 
                                     ProgramID = 'PROGRAM_ID',
                                     MembershipID = j)
            a3_1_3_4 = ET.SubElement(a3_1_3, 'ExcessBaggage', IssuerCode = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]),
                                     SerialNumber = k,
                                     SequenceCount = str(1), BaggagePool = "MP", 
                                     UnitOfMeasureQuantity = str(choices([1,2,3], [0.5, 0.3, 0.2])[0]),
                                     UnitOfMeasureCode = "Kg")
            a3_1_3_5 = ET.SubElement(a3_1_3, 'FareInfo', PTC_Code = 'PTC_CODE',
                                     DiscountedFareType = 'DISC_FARE_TYPE',
                                     DiscountrPercent = str(5), CountryCode = str(df_book.loc[df_book['initID'] == j, 'HH_ISO'].iloc[0]),
                                     DiscountedFareClassType = 'CABIN_CLASS',
                                     FareBasis = 'SFLY')
            a3_1_3_6 = ET.SubElement(a3_1_3, 'SSR', SSR_Code = 'OTHS',
                                     ServiceQuantity = str(1),Status = 'HN',
                                     BoardPoint = df_flight.loc[df_flight['flight_id'] == i, 'IATA_O'].iloc[0],
                                     OffPoint = df_flight.loc[df_flight['flight_id'] == i, 'IATA_D'].iloc[0],
                                     RPH = str(k),
                                     SurnameRefNumber = str(df_P.loc[df_P['P_ID'] == k, 'HHID'].iloc[0]))
            a3_1_3_6_1 = ET.SubElement(a3_1_3_6, 'Airline', Code = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
            a3_1_3_6_2 = ET.SubElement(a3_1_3_6, 'TEXT')
            a3_1_3_6_2.text = 'MADDOX/MOLLY'
            a3_1_3_7 = ET.SubElement(a3_1_3, 'TicketDocument', TicketDocumentNbr = str(i)+"/"+str(j)+"/"+str(k),
                                     Type = 'TICKET_TYPE',
                                     DateOfIssue = str(df_flight.loc[df_flight['flight_id'] == i, 'day'].iloc[0]),
                                     TicketLocation = df_flight.loc[df_flight['flight_id'] == i, 'IATA_O'].iloc[0],
                                     PrimaryDocInd = str(choices(['TRUE', 'FALSE'], [0.7, 0.3])[0]))
            a3_1_3_7_1 = ET.SubElement(a3_1_3_7, 'TotalFare', 
                                       Amount = str(12345),
                                       CurrencyCode = str(df_book.loc[df_book['initID'] == j, 'Currency'].iloc[0]))
            a3_1_3_7_2 = ET.SubElement(a3_1_3_7, 'PricingInfo', Date = str(df_flight.loc[df_flight['flight_id'] == i, 'day'].iloc[0]),
                                       Time = str(df_book.loc[df_book['initID'] == j, 'outboundDate'].iloc[0]),
                                       ISOCountryCode = str(df_book.loc[df_book['initID'] == j, 'HH_ISO'].iloc[0]),
                                       LocationCode = str(df_book.loc[df_book['initID'] == j, 'IATA'].iloc[0]),
                                       NonEndorsableInd = str(choices(['TRUE', 'FALSE'], [0.7, 0.3])[0]),
                                       NonRefundableInd = str(choices(['TRUE', 'FALSE'], [0.7, 0.3])[0]),
                                       PenaltyRestrictionInd = str(choices(['TRUE', 'FALSE'], [0.7, 0.3])[0]))
            a3_1_3_7_3 = ET.SubElement(a3_1_3_7, 'Taxes')
            a3_1_3_7_3_1 = ET.SubElement(a3_1_3_7_3, 'Tax', Amount = str(123),
                                         ISOCountry = str(df_book.loc[df_book['initID'] == j, 'HH_ISO'].iloc[0]),
                                         CurrencyCode = str(df_book.loc[df_book['initID'] == j, 'Currency'].iloc[0]),
                                         TaxType = "BK")
            primary_passenger = df_book.loc[df_book['initID'] == j, 'primary_passengers'].iloc[0]
            a3_1_3_7_4 = ET.SubElement(a3_1_3_7, 'PaymentInfo', PaymentType = 'CC', PaymentUse = 'NEW',
                                       PaymentAmount = str(12345),
                                       VendorCode = str(df_P.loc[df_P['P_ID'] == primary_passenger, 'PaymentInfo_VendorCode'].iloc[0]),
                                       AccountNbr = str(df_P.loc[df_P['P_ID'] == primary_passenger, 'PaymentInfo_AccountNbr'].iloc[0]),
                                       ExpiryDate = str(df_P.loc[df_P['P_ID'] == primary_passenger, 'PaymentInfo_ExpiryDate'].iloc[0]),
                                       CardHolderName = str(df_P.loc[df_P['P_ID'] == primary_passenger, 'FirstName'].iloc[0])+str(df_P.loc[df_P['P_ID'] == primary_passenger, 'Surname'].iloc[0]))
            a3_1_3_8 = ET.SubElement(a3_1_3, 'DOC_SSR', SSR_Code = 'DOCA',
                                     ServiceQuantity = str(1),
                                     Status = 'HK')
            a3_1_3_8_1 = ET.SubElement(a3_1_3_8, 'FlightInfo', Code = str(df_flight.loc[df_flight['flight_id'] == i, 'IATA_A'].iloc[0]))
            a3_1_3_8_2 = ET.SubElement(a3_1_3_8, 'DOCA', AddressType = "R",
                                      Address = str(df_P.loc[df_P['P_ID'] == k, 'Address'].iloc[0]),
                                      CityName = str(df_book.loc[df_book['initID'] == j, 'City'].iloc[0]),
                                      PostalCode = str(df_P.loc[df_P['P_ID'] == k, 'PostCode'].iloc[0]),
                                      StateProvCounty = 'STATE_PROV_COUNTY',
                                      Country = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]))
            a3_1_3_9 = ET.SubElement(a3_1_3, 'DOC_SSR', SSR_Code = 'DOCO',ServiceQuantity = str(1),Status = 'HK')
            a3_1_3_9_1 = ET.SubElement(a3_1_3_9, 'DOCO', BirthLocation = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]),
                                       TravelDocType = 'V',
                                       TravelDocNbr = str(k),
                                       PlaceOfIssue = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]),
                                       DateOfIssue = "-",
                                       CountryState = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]))
            a3_1_3_10 = ET.SubElement(a3_1_3, 'DOC_SSR', SSR_Code = 'DOCS',ServiceQuantity = str(1),Status = 'HK')
            a3_1_3_10_1 = ET.SubElement(a3_1_3_10, 'DOCS', DateOfBirth = str(df_P.loc[df_P['P_ID'] == k, 'DOB'].iloc[0]),
                                        ExpiryDate = str(df_P.loc[df_P['P_ID'] == k, 'DOCS_ExpiryDate'].iloc[0]),
                                        FirstGivenName = str(df_P.loc[df_P['P_ID'] == k, 'FirstName'].iloc[0]),
                                        SecondGivenName = "",
                                        Surname = str(df_P.loc[df_P['P_ID'] == k, 'Surname'].iloc[0]),
                                        Gender = str(df_P.loc[df_P['P_ID'] == k, 'P_GENDER'].iloc[0]),
                                        IssuingLoc = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]),
                                        PaxNationality = str(df_P.loc[df_P['P_ID'] == k, 'Country'].iloc[0]))
        fly = 1
#         print(j)
#         print(len(df_book.loc[df_book['initID'] == j, 'allFlights'].iloc[0]))
        for l in  df_book.loc[df_book['initID'] == j, 'allFlights'].iloc[0]:
            
            a3_1_4 = ET.SubElement(a3_1, 'Flight', 
                                   DepartureDateTime= str(df_flight.loc[df_flight['flight_id'] == l, 'firstseen'].iloc[0]),
                                   ArrivalDateTime = str(df_flight.loc[df_flight['flight_id'] == l, 'lastseen'].iloc[0]),
                                   ResBookDesigCode = "S",
                                   NumberInParty = str(df_book.loc[df_book['initID'] == j, 'num_in_party'].iloc[0]),
                                   Status = "HK",
                                   FlightNumber = str(fly))
            a3_1_4_1 = ET.SubElement(a3_1_4, 'DepartureAirport', LocationCode = str(df_flight.loc[df_flight['flight_id'] == l, 'IATA_O'].iloc[0]))
            a3_1_4_2 = ET.SubElement(a3_1_4, 'ArrivalAirport', LocationCode = str(df_flight.loc[df_flight['flight_id'] == l, 'IATA_D'].iloc[0]))
            a3_1_4_3 = ET.SubElement(a3_1_4, 'OperatingAirline', Code = str(df_flight.loc[df_flight['flight_id'] == l, 'IATA_A'].iloc[0]),
                                    FlightNumber = str(df_flight.loc[df_flight['flight_id'] == l, 'flightNbr'].iloc[0]),
                                    ResBookDesigCode = "S")
            a3_1_4_4 = ET.SubElement(a3_1_4, 'MarketingAirline', Code = "TX")
            
            fly = fly+1
            
    
    
    tree = ET.ElementTree(root)    
    filename = 'XML_DATAV2/'+str(i)+".xml"        
      
    with open (filename, "wb") as file :
        file.write(ET.tostring(root,encoding='UTF-8'))

In [41]:
df_flight[df_flight['flight_id'] == 141248]['bookings'].tolist()

['MUC-LGW-business-ID1,MUC-LGW-business-ID59,MUC-LGW-business-ID89,MUC-LGW-business-ID105,MUC-LGW-group-ID42,MUC-INN-business-ID0,MUC-LGW-leisure-ID9,MUC-LGW-leisure-ID61,MUC-LGW-leisure-ID69,MUC-JER-leisure-ID0,MUC-LGW-leisure-ID81,MUC-LGW-leisure-ID175,MUC-LGW-leisure-ID182,MUC-LGW-leisure-ID196,MUC-LGW-leisure-ID213,MUC-LGW-leisure-ID233,MUC-LGW-leisure-ID251,MUC-LGW-leisure-ID258,MUC-JER-leisure-ID7,MUC-LGW-leisure-ID311,MUC-LGW-leisure-ID328,MUC-LGW-leisure-ID366,MUC-LGW-leisure-ID390,MUC-LGW-leisure-ID522,MUC-LGW-leisure-ID544,MUC-LGW-leisure-ID585,MUC-LGW-leisure-ID618,MUC-LGW-leisure-ID672,MUC-LGW-leisure-ID747,MUC-LGW-leisure-ID748,MUC-JER-leisure-ID23,MUC-LGW-leisure-ID868,MUC-LGW-leisure-ID882,MUC-LGW-leisure-ID978,MUC-INN-leisure-ID19,MUC-LGW-leisure-ID1024,MUC-LGW-leisure-ID1043,MUC-LGW-leisure-ID1045,MUC-LGW-leisure-ID1048,MUC-LGW-leisure-ID1119,LGW-MUC-business-ID12,RIX-MUC-leisure-ID79,LGW-MUC-leisure-ID340,LGW-MUC-leisure-ID535,LGW-MUC-leisure-ID560,LGW-MUC-leisure-ID5

In [19]:
df_flight_POI

65986

In [ ]:
str(df_P.loc[df_P['P_ID'] == k, 'HHID'].iloc[0])

In [ ]:
df_P[df_P['P_ID'] == k]

In [92]:
df_book_POI

Unnamed: 0           initID      list_of_passengers  stayDay    route  \
0           1  MUC-LGW-POI-ID0             ['POI_1_1']      NaN  MUC-LGW   
1           2  OTP-LGW-POI-ID0  ['POI_2_1', 'POI_2_2']      NaN  OTP-LGW   
2           3  ARN-BRS-POI-ID0  ['POI_3_1', 'POI_3_2']      NaN  ARN-BRS   
3           4  RIX-NOC-POI-ID0             ['POI_4_1']      NaN  RIX-NOC   
4           8  ZAG-HAM-POI-ID0  ['POI_8_1', 'POI_8_2']      NaN  ZAG-HAM   
5           9  OTP-LHR-POI-ID0             ['POI_9_1']      NaN  OTP-LHR   

   num_in_party       fixRoute  Leg_fixRoute LegHH_ISO  Airport_Itinerary_Out  \
0             1       MUC->LGW           1.0   DEU-GBR         ['MUC', 'LGW']   
1             2       OTP->LGW           1.0   ROU-GBR         ['OTP', 'LGW']   
2             2  ARN->AMS->BRS           2.0   SWE-GBR  ['ARN', 'AMS', 'BRS']   
3             1  RIX->STN->NOC           2.0   LVA-IRL  ['RIX', 'STN', 'NOC']   
4             2  ZAG->LHR->HAM           2.0   HRV-DEU  ['ZAG', 'LHR', 'HAM']   
5             1       OTP->LHR           1.0   ROU-GBR         ['OTP', 'LHR']   

              full_routes               outboundDate  returnDate  \
0             ['MUC-LGW']  2019-03-20 00:00:00+00:00         NaN   
1             ['OTP-LGW']  2019-03-10 00:00:00+00:00         NaN   
2  ['ARN-AMS', 'AMS-BRS']  2019-03-21 00:00:00+00:00         NaN   
3  ['RIX-STN', 'STN-NOC']  2019-03-07 00:00:00+00:00         NaN   
4  ['ZAG-LHR', 'LHR-HAM']  2019-03-26 00:00:00+00:00         NaN   
5             ['OTP-LHR']  2019-03-31 00:00:00+00:00         NaN   

    outboundFlights  Airport_Itinerary_Ret           return_routes  \
0          [141248]         ['LGW', 'MUC']             ['LGW-MUC']   
1           [74802]         ['LGW', 'OTP']             ['LGW-OTP']   
2  [151717, 153090]  ['BRS', 'AMS', 'ARN']  ['BRS-AMS', 'AMS-ARN']   
3      [53398, nan]  ['NOC', 'STN', 'RIX']  ['NOC-STN', 'STN-RIX']   
4  [184710, 185978]  ['HAM', 'LHR', 'ZAG']  ['HAM-LHR', 'LHR-ZAG']   
5          [217108]         ['LHR', 'OTP']             ['LHR-OTP']   

  returnFlights  
0         [nan]  
1         [nan]  
2    [nan, nan]  
3    [nan, nan]  
4    [nan, nan]  
5         [nan]

In [100]:
df_flight.to_csv('buildXML/DB/flights.csv')
df_P.to_csv('buildXML/DB/passenger.csv')
df_book.to_csv('buildXML/DB/bookings.csv')

In [101]:
df_P.tail(20)

Unnamed: 0      P_num        HHID          P_ID  P_AGE AgeRange  \
2529584     2529584  2529585.0  GBR_119180  GBR_119180_1     71    70-74   
2529585     2529585  2529586.0  GBR_119181  GBR_119181_1     69    65-69   
2529586     2529586  2529587.0  GBR_119182  GBR_119182_1     65    65-69   
2529587           0        NaN       POI_0       POI_0_1     36    35-39   
2529588           1        NaN       POI_0       POI_0_2     15    15-19   
2529589           2        NaN       POI_1       POI_1_1     13    10-14   
2529590           3        NaN       POI_2       POI_2_1     29    25-29   
2529591           4        NaN       POI_2       POI_2_2     12    10-14   
2529592           5        NaN       POI_3       POI_3_1     46    45-49   
2529593           6        NaN       POI_3       POI_3_2      7      5-9   
2529594           7        NaN       POI_4       POI_4_1      9      5-9   
2529595           8        NaN       POI_5       POI_5_1     51    50-54   
2529596           9        NaN       POI_5       POI_5_2     10    10-14   
2529597          10        NaN       POI_6       POI_6_1     36    35-39   
2529598          11        NaN       POI_6       POI_6_2      6      5-9   
2529599          12        NaN       POI_7       POI_7_1     47    45-49   
2529600          13        NaN       POI_7       POI_7_2      5      5-9   
2529601          14        NaN       POI_8       POI_8_1     32    30-34   
2529602          15        NaN       POI_8       POI_8_2     10    10-14   
2529603          16        NaN       POI_9       POI_9_1      9      5-9   

        AgeGroup P_GENDER HH_ISO GenderHOH  ...  PostCode  \
2529584    AGE15        F    GBR         F  ...  NR58 1TP   
2529585    AGE14        F    GBR         F  ...   E6J 6LN   
2529586    AGE14        M    GBR         M  ...  MK71 0AG   
2529587     AGE8        M    IRL         M  ...     17045   
2529588     AGE4        M    IRL         M  ...     17045   
2529589     AGE3        M    DEU         M  ...     30274   
2529590     AGE6        F    ROU         F  ...    904976   
2529591     AGE3        M    ROU         F  ...    904976   
2529592    AGE10        M    SWE         M  ...     54847   
2529593     AGE2        M    SWE         M  ...     54847   
2529594     AGE2        F    LVA         F  ...     24248   
2529595    AGE11        M    CHE         M  ...      5788   
2529596     AGE3        M    CHE         M  ...      5788   
2529597     AGE8        F    BEL         F  ...      6450   
2529598     AGE2        M    BEL         F  ...      6450   
2529599    AGE10        M    SVK         M  ...    946 93   
2529600     AGE2        M    SVK         M  ...    946 93   
2529601     AGE7        M    HRV         M  ...     89437   
2529602     AGE3        M    HRV         M  ...     89437   
2529603     AGE2        M    ROU         M  ...    586889   

                     Country                         FreeEmail  \
2529584       United Kingdom               bclarke@hotmail.com   
2529585       United Kingdom                gary54@outlook.com   
2529586       United Kingdom          hannahwright@outlook.com   
2529587  Republic of Ireland          graceo-fuada@hotmail.com   
2529588  Republic of Ireland          o-madagainrita@gmail.com   
2529589              Germany           qmac-aonghais@yahoo.com   
2529590              Romania        o-goillidheronan@gmail.com   
2529591              Romania   o-conghamhnasuzanne@hotmail.com   
2529592               Sweden     o-flanagainthaddeus@gmail.com   
2529593               Sweden                                 -   
2529594        United States                                 -   
2529595          Switzerland  mac-robhartaighelena@hotmail.com   
2529596          Switzerland         o-laoidermott@hotmail.com   
2529597              Belgium     fmac-giolla-easboig@gmail.com   
2529598              Belgium                                 -   
2529599             Slovakia         basilo-meadog@hotmail.com   
2529600 